# Are Complicated Recipes Unhealthy and Boring?

**Name(s)**: Brian Liu

**Website Link**: https://brianzliu.github.io/recipes-nutritional-analysis/

In [1]:
import pandas as pd
import numpy as np
from pathlib import Path
import ast
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.metrics import mean_squared_error

import plotly.express as px
pd.options.plotting.backend = 'plotly'

# from dsc80_utils import * # Feel free to uncomment and use this.

## Step 1: Introduction

**Question to Explore**: How does the complexity of the recipe (i.e. # of steps) affect the nutritional value and recipe rating?

## Step 2: Data Cleaning and Exploratory Data Analysis

### Data Cleaning

In [2]:
recipes = pd.read_csv("RAW_recipes.csv")
interactions = pd.read_csv("RAW_interactions.csv")

In [3]:
recipes_interactions = recipes.merge(interactions, left_on='id', right_on='recipe_id', how='left')
recipes_interactions['rating'] = recipes_interactions['rating'].apply(lambda x: np.nan if x == 0.0 else x)
recipes_interactions_recipe_rating_avg = recipes_interactions.groupby('name')['rating'].mean()
recipes_interactions_recipe_rating_avg = recipes_interactions_recipe_rating_avg.rename('rating_avg')
recipes_interactions = recipes_interactions.merge(recipes_interactions_recipe_rating_avg, left_on='name', right_index=True, how='left')
recipes_interactions

name      id  minutes  \
0               1 brownies in the world    best ever  333281       40   
1                 1 in canada chocolate chip cookies  453467       45   
2                             412 broccoli casserole  306168       40   
3                             412 broccoli casserole  306168       40   
4                             412 broccoli casserole  306168       40   
...                                              ...     ...      ...   
234424                     zydeco ya ya deviled eggs  308080       40   
234425        cookies by design   cookies on a stick  298512       29   
234426  cookies by design   sugar shortbread cookies  298509       20   
234427  cookies by design   sugar shortbread cookies  298509       20   
234428  cookies by design   sugar shortbread cookies  298509       20   

        contributor_id   submitted  \
0               985201  2008-10-27   
1              1848091  2011-04-11   
2                50969  2008-05-30   
3                50969  2008-05-30   
4                50969  2008-05-30   
...                ...         ...   
234424           37779  2008-06-07   
234425          506822  2008-04-15   
234426          506822  2008-04-15   
234427          506822  2008-04-15   
234428          506822  2008-04-15   

                                                     tags  \
0       ['60-minutes-or-less', 'time-to-make', 'course...   
1       ['60-minutes-or-less', 'time-to-make', 'cuisin...   
2       ['60-minutes-or-less', 'time-to-make', 'course...   
3       ['60-minutes-or-less', 'time-to-make', 'course...   
4       ['60-minutes-or-less', 'time-to-make', 'course...   
...                                                   ...   
234424  ['60-minutes-or-less', 'time-to-make', 'course...   
234425  ['30-minutes-or-less', 'time-to-make', 'course...   
234426  ['30-minutes-or-less', 'time-to-make', 'course...   
234427  ['30-minutes-or-less', 'time-to-make', 'course...   
234428  ['30-minutes-or-less', 'time-to-make', 'course...   

                                           nutrition  n_steps  \
0           [138.4, 10.0, 50.0, 3.0, 3.0, 19.0, 6.0]       10   
1       [595.1, 46.0, 211.0, 22.0, 13.0, 51.0, 26.0]       12   
2          [194.8, 20.0, 6.0, 32.0, 22.0, 36.0, 3.0]        6   
3          [194.8, 20.0, 6.0, 32.0, 22.0, 36.0, 3.0]        6   
4          [194.8, 20.0, 6.0, 32.0, 22.0, 36.0, 3.0]        6   
...                                              ...      ...   
234424          [59.2, 6.0, 2.0, 3.0, 6.0, 5.0, 0.0]        7   
234425     [188.0, 11.0, 57.0, 11.0, 7.0, 21.0, 9.0]        9   
234426      [174.9, 14.0, 33.0, 4.0, 4.0, 11.0, 6.0]        5   
234427      [174.9, 14.0, 33.0, 4.0, 4.0, 11.0, 6.0]        5   
234428      [174.9, 14.0, 33.0, 4.0, 4.0, 11.0, 6.0]        5   

                                                    steps  \
0       ['heat the oven to 350f and arrange the rack i...   
1       ['pre-heat oven the 350 degrees f', 'in a mixi...   
2       ['preheat oven to 350 degrees', 'spray a 2 qua...   
3       ['preheat oven to 350 degrees', 'spray a 2 qua...   
4       ['preheat oven to 350 degrees', 'spray a 2 qua...   
...                                                   ...   
234424  ['in a bowl , combine the mashed yolks and may...   
234425  ['place melted butter in a large mixing bowl a...   
234426  ['whip sugar and shortening in a large bowl , ...   
234427  ['whip sugar and shortening in a large bowl , ...   
234428  ['whip sugar and shortening in a large bowl , ...   

                                              description  \
0       these are the most; chocolatey, moist, rich, d...   
1       this is the recipe that we use at my school ca...   
2       since there are already 411 recipes for brocco...   
3       since there are already 411 recipes for brocco...   
4       since there are already 411 recipes for brocco...   
...                                                   ...   
234424                          deviled 

### Nutritional Feature Extractions

In [4]:
# Making separate columns for each nutritional value
ri_custom = recipes_interactions.copy()
ri_custom['nutrition'] = ri_custom['nutrition'].apply(ast.literal_eval) # converts each list-like string in nutrition column into actual list

# Define the column names in order
nutrition_columns = [
    'calories (#)',
    'total fat (PDV)',
    'sugar (PDV)',
    'sodium (PDV)',
    'protein (PDV)',
    'saturated fat (PDV)',
    'carbohydrates (PDV)'
]

# create a dataframe with the separate nutrition columns
nutrition_df = pd.DataFrame(ri_custom['nutrition'].tolist(), columns=nutrition_columns, index=ri_custom.index)

# assign each column to ri_custom
for col in nutrition_columns:
    ri_custom[col] = nutrition_df[col]

ri_custom.head(4)

name      id  minutes  contributor_id  \
0  1 brownies in the world    best ever  333281       40          985201   
1    1 in canada chocolate chip cookies  453467       45         1848091   
2                412 broccoli casserole  306168       40           50969   
3                412 broccoli casserole  306168       40           50969   

    submitted                                               tags  \
0  2008-10-27  ['60-minutes-or-less', 'time-to-make', 'course...   
1  2011-04-11  ['60-minutes-or-less', 'time-to-make', 'cuisin...   
2  2008-05-30  ['60-minutes-or-less', 'time-to-make', 'course...   
3  2008-05-30  ['60-minutes-or-less', 'time-to-make', 'course...   

                                      nutrition  n_steps  \
0      [138.4, 10.0, 50.0, 3.0, 3.0, 19.0, 6.0]       10   
1  [595.1, 46.0, 211.0, 22.0, 13.0, 51.0, 26.0]       12   
2     [194.8, 20.0, 6.0, 32.0, 22.0, 36.0, 3.0]        6   
3     [194.8, 20.0, 6.0, 32.0, 22.0, 36.0, 3.0]        6   

                                               steps  \
0  ['heat the oven to 350f and arrange the rack i...   
1  ['pre-heat oven the 350 degrees f', 'in a mixi...   
2  ['preheat oven to 350 degrees', 'spray a 2 qua...   
3  ['preheat oven to 350 degrees', 'spray a 2 qua...   

                                         description  ... rating  \
0  these are the most; chocolatey, moist, rich, d...  ...    4.0   
1  this is the recipe that we use at my school ca...  ...    5.0   
2  since there are already 411 recipes for brocco...  ...    5.0   
3  since there are already 411 recipes for brocco...  ...    5.0   

                                              review  rating_avg  \
0  These were pretty good, but took forever to ba...         4.0   
1  Originally I was gonna cut the recipe in half ...         5.0   
2  This was one of the best broccoli casseroles t...         5.0   
3  I made this for my son's first birthday party ...         5.0   

   calories (#) total fat (PDV)  sugar (PDV) sodium (PDV)  protein (PDV)  \
0         138.4            10.0         50.0          3.0            3.0   
1         595.1            46.0        211.0         22.0           13.0   
2         194.8            20.0          6.0         32.0           22.0   
3         194.8            20.0          6.0         32.0           22.0   

   saturated fat (PDV)  carbohydrates (PDV)  
0                 19.0                  6.0  
1                 51.0                 26.0  
2                 36.0                  3.0  
3                 36.0                  3.0  

[4 rows x 25 columns]

### Univariate Analysis

In [96]:
fig = px.histogram(ri_custom, 'rating_avg', nbins=5, title="Distribution of Recipes' Average Rating")
fig.show()

In [99]:
fig = px.histogram(ri_custom, 'n_steps', title="Distribution of Recipes' # of Steps")
fig.show()

### Bivariate Analysis

In [102]:
fig = px.scatter(ri_custom, x='n_steps', y='calories (#)', title='Distribution of Calories (#) for each n_steps')
fig.add_vline(ri_custom['n_steps'].median(), annotation_text='median number of steps', line_color='red', line_dash='dash')
fig.show()

In [105]:
fig = px.scatter(ri_custom, x='saturated fat (PDV)', y='rating_avg', title='Distribution of Average Ratings per PDV Saturated Fat')
fig.add_vline(ri_custom['saturated fat (PDV)'].median(), annotation_text='median saturated fat (PDV)', line_color='red', line_dash='dash')
fig.add_hline(ri_custom['rating_avg'].median(), annotation_text='median average rating', line_color='red', line_dash='dash')
fig.show()

### Interesting Aggregates

In [107]:
# group by number of steps and calculate average rating
agg_rating_by_steps = ri_custom.groupby('n_steps').agg({
    'rating_avg': 'mean',
    'id': 'count'
}).rename(columns={'id': 'count'})

agg_rating_by_steps = agg_rating_by_steps[agg_rating_by_steps['count'] > 10] # filter step counts > 10 to remove noise

agg_rating_by_steps = agg_rating_by_steps.sort_values('n_steps')

agg_rating_by_steps.sort_values('rating_avg', ascending=False).head()

print(agg_rating_by_steps.sort_values('rating_avg', ascending=False).head().to_markdown())

|   n_steps |   rating_avg |   count |
|----------:|-------------:|--------:|
|        39 |      4.93333 |      15 |
|        33 |      4.92308 |      41 |
|        40 |      4.89583 |      16 |
|        28 |      4.88991 |     157 |
|        50 |      4.84615 |      13 |


In [108]:
fig = px.scatter(agg_rating_by_steps,
                 x=agg_rating_by_steps.index,
                 y='rating_avg',
                 trendline='ols',
                 title='Average Rating vs. Number of Steps',
                 labels={'n_steps': 'Number of Steps', 'rating_avg': 'Average Rating'})
fig.update_layout(width=800, height=480) # Adjust figure size for better display
fig.show()

In [111]:
# Create a categorical column for complexity based on quartiles or fixed bins
# Example bins: 1-5 (Low), 6-10 (Medium), 11-20 (High), 20+ (Very High)
ri_custom['complexity_level'] = pd.cut(ri_custom['n_steps'], 
                                     bins=[0, 5, 10, 20, 100], 
                                     labels=['Low (1-5)', 'Medium (6-10)', 'High (11-20)', 'Very High (20+)'])

# Pivot table showing average Calories, Sugar, and Fat for each complexity level
# This directly addresses the "nutritional value" part of your research question
agg_nutrition_by_complexity = ri_custom.pivot_table(
    index='complexity_level',
    values=['calories (#)', 'sugar (PDV)', 'total fat (PDV)'],
    aggfunc='mean'
)

print(agg_nutrition_by_complexity.to_markdown())

| complexity_level   |   calories (#) |   sugar (PDV) |   total fat (PDV) |
|:-------------------|---------------:|--------------:|------------------:|
| Low (1-5)          |        314.382 |       60.1612 |           23.2877 |
| Medium (6-10)      |        400.095 |       59.9385 |           30.1355 |
| High (11-20)       |        480.959 |       67.4381 |           36.8632 |
| Very High (20+)    |        637.803 |       87.1659 |           50.491  |


/var/folders/ng/bts1b1qn5_gfyd59gql9sf2m0000gn/T/ipykernel_97029/1751862169.py:9: FutureWarning:

The default value of observed=False is deprecated and will change to observed=True in a future version of pandas. Specify observed=False to silence this warning and retain the current behavior



In [64]:
ri_custom = ri_custom.sample(frac=1).head(50000)
ri_custom.to_csv('ri_custom.csv')

## Step 3: Assessment of Missingness

**Goal:** Examine if the missingness of the 'rating' column depends on 'n_steps' and 'minutes'

### Missingness Dependency ('n_steps')

In [70]:
ri_custom['rating_missing'] = ri_custom['rating'].isna()

mean_missing = ri_custom[ri_custom['rating_missing']]['n_steps'].mean()
mean_present = ri_custom[~ri_custom['rating_missing']]['n_steps'].mean()
observed_diff = abs(mean_missing - mean_present)

print(f'Mean n_steps (Rating Missing): {mean_missing}')
print(f'Mean n_steps (Rating Present): {mean_present}')
print(f'Observed Statistic: {observed_diff}')

n_permutations = 1000
simulated_diffs = []

shuffled_missing_pooled = ri_custom['rating_missing'].values
n_steps_values = ri_custom['n_steps'].values

for _ in range(n_permutations):
    shuffled_missing = np.random.permutation(shuffled_missing_pooled)
    
    mean_m = n_steps_values[shuffled_missing].mean()
    mean_p = n_steps_values[~shuffled_missing].mean()
    
    simulated_diffs.append(abs(mean_m - mean_p))

p_value = (np.array(simulated_diffs) >= observed_diff).mean()
print(f'p-value: {p_value}')

# plotting
fig = px.histogram(pd.DataFrame({'simulated_diffs': simulated_diffs}), x='simulated_diffs', title='Empirical Distribution of the Test Statistic')
fig.add_vline(x=observed_diff, line_color='red', annotation_text='Observed Statistic')
fig.show()

Mean n_steps (Rating Missing): 11.311985361390668
Mean n_steps (Rating Present): 9.939877143040603
Observed Statistic: 1.372108218350066
p-value: 0.0


### Missingness Non-dependency ('minutes')

In [71]:
ri_custom['rating_missing'] = ri_custom['rating'].isna()

mean_missing = ri_custom[ri_custom['rating_missing']]['minutes'].mean()
mean_present = ri_custom[~ri_custom['rating_missing']]['minutes'].mean()
observed_diff = abs(mean_missing - mean_present)

print(f'Mean minutes (Rating Missing): {mean_missing}')
print(f'Mean minutes (Rating Present): {mean_present}')
print(f'Observed Statistic: {observed_diff}')

n_permutations = 1000
simulated_diffs = []

shuffled_missing_pooled = ri_custom['rating_missing'].values
minutes_values = ri_custom['minutes'].values

for _ in range(n_permutations):
    shuffled_missing = np.random.permutation(shuffled_missing_pooled)
    
    mean_m = minutes_values[shuffled_missing].mean()
    mean_p = minutes_values[~shuffled_missing].mean()
    
    simulated_diffs.append(abs(mean_m - mean_p))

p_value = (np.array(simulated_diffs) >= observed_diff).mean()
print(f'p-value: {p_value}')

# plotting
fig = px.histogram(pd.DataFrame({'simulated_diffs': simulated_diffs}), x='simulated_diffs', title='Empirical Distribution of the Test Statistic')
fig.add_vline(x=observed_diff, line_color='red', annotation_text='Observed Statistic')
fig.show()

Mean minutes (Rating Missing): 123.0051845074718
Mean minutes (Rating Present): 98.92748442884356
Observed Statistic: 24.07770007862824
p-value: 0.129


## Step 4: Hypothesis Testing
### Pair of Hypotheses
**Null Hypothesis:** Recipes with 10+ steps and recipes with <10 steps are equal in average calories.

**Alternative Hypothesis:** Recipes with 10+ steps have higher average calories than recipes with <10 steps.

**Test Statistic:** Difference between mean calories of recipes with 10+ steps and mean calories with <10 steps.

### Ad Hoc Data Preprocessing

In [85]:
ri_custom_calories_nsteps = ri_custom.loc[:, ['n_steps', 'calories (#)']]
ri_custom_calories_nsteps['>=10 steps'] = ri_custom_calories_nsteps['n_steps'] >= 10

### Permutation Testing

In [86]:
observed_stat_df = ri_custom_calories_nsteps.groupby('>=10 steps').mean()

observed_diff = observed_stat_df.loc[True, 'calories (#)'] - observed_stat_df.loc[False, 'calories (#)']
observed_diff

np.float64(126.25445103155084)

In [87]:
n_permutations = 1000
permuted_diffs = []

shuffled_df = ri_custom_calories_nsteps.copy()

for _ in range(n_permutations):
    shuffled_df['shuffled_calories (#)'] = np.random.permutation(shuffled_df['calories (#)'])
    shuffled_calorie_means = shuffled_df.groupby('>=10 steps')['shuffled_calories (#)'].mean()
    permuted_diffs.append(shuffled_calorie_means.loc[True] - shuffled_calorie_means.loc[False])

In [88]:
p_value = (np.array(permuted_diffs) >= observed_diff).mean()
p_value

np.float64(0.0)

## Step 5: Framing a Prediction Problem
### Problem Identificaton
**Problem Type**: Regression

**Response Variable**: rating_avg. The reason I chose average rating is because I want to understand the relationship between a recipe's complexity and nutritional value with its perceived quality

**Evaluation Metric**: RMSE; I chose RMSE over other metrics like $R^2$ as RMSE is more interpretable in the same units as the average ratings, and RMSE penalizes large errors more heavily, which is important to consider for user satisfaction.

**Predictor Variables**: 
- Baseline Model: calories and n_steps. Since these variables are known before any user rates the recipe, they are valid variables to predict average rating.

## Step 6: Baseline Model

In [89]:
ri_custom_valid_rating = ri_custom.dropna(subset=['rating_avg'])

In [93]:
X = ri_custom_valid_rating.loc[:, ['n_steps', 'calories (#)']]
y = ri_custom_valid_rating.loc[:, 'rating_avg']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=42)

preprocessing = ColumnTransformer(
    transformers=[
        ('scaling', StandardScaler(), ['n_steps', 'calories (#)'])
    ],
    remainder='drop'
)

baseline_model = Pipeline([
    ('preprocessing', preprocessing),
    ('regression', LinearRegression())
])

baseline_model.fit(X_train, y_train)

y_pred_train = baseline_model.predict(X_train)
y_pred_test = baseline_model.predict(X_test)

rmse_train = np.sqrt(mean_squared_error(y_train, y_pred_train))
rmse_test = np.sqrt(mean_squared_error(y_test, y_pred_test))

print(f'Train RMSE: {rmse_train}')
print(f'Test RMSE: {rmse_test}')

Train RMSE: 0.49623102267797653
Test RMSE: 0.493720400573423


## Step 7: Final Model

### Hyperparameter Tuning and Final Model
We will use a **RandomForestRegressor** as our final model. 
We chose this model because it can capture non-linear relationships and interactions between features better than a simple linear model.

**Features Added:**
- `minutes`: Preparation time is a key factor in recipe complexity.
- `n_ingredients`: More ingredients usually imply more complexity.
- `total fat (PDV)`, `sugar (PDV)`, `protein (PDV)`: Nutritional components that might correlate with "unhealthy" or "tasty" ratings.

**Preprocessing:**
- **QuantileTransformer**: Applied to `minutes` and `calories (#)` to handle skewness and outliers.
- **StandardScaler**: Applied to other numerical features to normalize their range.

**Hyperparameters to Tune:**
- `n_estimators`: Number of trees in the forest. We will try [50, 100].
- `max_depth`: Maximum depth of the tree. We will try [5, 10, 15] to control overfitting.
- `min_samples_split`: Minimum number of samples required to split an internal node. We will try [2, 5].

In [94]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.preprocessing import QuantileTransformer

# 1. Define X and y with new features
features = ['n_steps', 'calories (#)', 'minutes', 'n_ingredients', 'total fat (PDV)', 'sugar (PDV)', 'protein (PDV)']
X_final = ri_custom_valid_rating[features]
y_final = ri_custom_valid_rating['rating_avg']

# 2. Train-test split (same random_state to ensure same split as baseline)
X_train_final, X_test_final, y_train_final, y_test_final = train_test_split(X_final, y_final, test_size=0.25, random_state=42)

# 3. Preprocessing pipeline
preprocessing_final = ColumnTransformer(
    transformers=[
        ('quantile', QuantileTransformer(output_distribution='normal'), ['minutes', 'calories (#)']),
        ('scaling', StandardScaler(), ['n_steps', 'n_ingredients', 'total fat (PDV)', 'sugar (PDV)', 'protein (PDV)'])
    ],
    remainder='drop'
)

final_pipeline = Pipeline([
    ('preprocessing', preprocessing_final),
    ('regression', RandomForestRegressor(random_state=42))
])

# 4. Hyperparameter Tuning
param_grid = {
    'regression__n_estimators': [50, 100],
    'regression__max_depth': [5, 10, 15],
    'regression__min_samples_split': [2, 5]
}

grid_search = GridSearchCV(final_pipeline, param_grid, cv=3, scoring='neg_root_mean_squared_error', n_jobs=-1)
grid_search.fit(X_train_final, y_train_final)

# 5. Best Model and Evaluation
best_model = grid_search.best_estimator_

print("Best Hyperparameters:", grid_search.best_params_)

y_pred_train_final = best_model.predict(X_train_final)
y_pred_test_final = best_model.predict(X_test_final)

rmse_train_final = np.sqrt(mean_squared_error(y_train_final, y_pred_train_final))
rmse_test_final = np.sqrt(mean_squared_error(y_test_final, y_pred_test_final))

print(f'Final Model Train RMSE: {rmse_train_final}')
print(f'Final Model Test RMSE: {rmse_test_final}')

# Comparison
# Assuming rmse_test from baseline is available as variable 'rmse_test'
# If not, we can't print the difference, but the values are printed above.
try:
    print(f"Improvement over Baseline (Test RMSE): {rmse_test - rmse_test_final}")
except NameError:
    print("Baseline RMSE variable not found for comparison.")

Best Hyperparameters: {'regression__max_depth': 15, 'regression__min_samples_split': 2, 'regression__n_estimators': 100}
Final Model Train RMSE: 0.3768828034399456
Final Model Test RMSE: 0.467404748235399
Improvement over Baseline (Test RMSE): 0.026315652338023965


## Step 8: Fairness Analysis

### Fairness Analysis
**Question:** Does our model perform differently for "Short" recipes (< 30 minutes) vs. "Long" recipes (>= 30 minutes)?

**Groups:**
- **Group X:** Short recipes (`minutes` < 30)
- **Group Y:** Long recipes (`minutes` >= 30)

**Evaluation Metric:** Root Mean Squared Error (RMSE)

**Hypotheses:**
- **Null Hypothesis:** The model's RMSE for Short and Long recipes are roughly the same, and any differences are due to random chance.
- **Alternative Hypothesis:** The model's RMSE for Short and Long recipes are significantly different.

**Test Statistic:** Absolute Difference in RMSE.

In [95]:
# 1. Create a validation DataFrame
# We use X_test_final and y_test_final from Step 7
test_results = X_test_final.copy()
test_results['rating_actual'] = y_test_final
test_results['rating_pred'] = y_pred_test_final

# 2. Define Groups
test_results['is_short'] = test_results['minutes'] < 30

# 3. Calculate Observed RMSEs
def calculate_rmse(df):
    return np.sqrt(mean_squared_error(df['rating_actual'], df['rating_pred']))

rmse_short = calculate_rmse(test_results[test_results['is_short']])
rmse_long = calculate_rmse(test_results[~test_results['is_short']])

observed_diff_rmse = abs(rmse_short - rmse_long)

print(f"RMSE (Short): {rmse_short}")
print(f"RMSE (Long): {rmse_long}")
print(f"Observed Absolute Difference: {observed_diff_rmse}")

# 4. Permutation Test
n_permutations = 500
simulated_diffs_rmse = []

shuffled_labels_pool = test_results['is_short'].values

for _ in range(n_permutations):
    # Shuffle the group labels
    shuffled_labels = np.random.permutation(shuffled_labels_pool)
    
    # Assign shuffled labels temporarily
    # We can just filter the original dataframe using the shuffled boolean array
    group_a = test_results[shuffled_labels]
    group_b = test_results[~shuffled_labels]
    
    rmse_a = calculate_rmse(group_a)
    rmse_b = calculate_rmse(group_b)
    
    simulated_diffs_rmse.append(abs(rmse_a - rmse_b))

# 5. P-value
p_value_fairness = (np.array(simulated_diffs_rmse) >= observed_diff_rmse).mean()
print(f"P-value: {p_value_fairness}")

# Conclusion
if p_value_fairness < 0.05:
    print("Conclusion: Reject the null hypothesis. The model is unfair with respect to recipe duration.")
else:
    print("Conclusion: Fail to reject the null hypothesis. We do not have evidence that the model is unfair based on recipe duration.")

# Plot
fig = px.histogram(pd.DataFrame({'diffs': simulated_diffs_rmse}), x='diffs', title='Empirical Distribution of RMSE Difference (Absolute)')
fig.add_vline(x=observed_diff_rmse, line_color='red', annotation_text='Observed Diff')
fig.show()

RMSE (Short): 0.4447006474064274
RMSE (Long): 0.4808216603505425
Observed Absolute Difference: 0.03612101294411513
P-value: 0.032
Conclusion: Reject the null hypothesis. The model is unfair with respect to recipe duration.


In [ ]:
# TODO